# Introduction

**This demo shows to run a distributed simulation of protein folding using GROMACS within a bittensor subnet**

In this subnet:
- Validators select a protein (pbd_id), download the structure and preprare input files
- Miners run the simulation and send back their results
- Scoring is based on free energy of the folded structure

In [14]:
import sys
import bittensor as bt

from typing import Tuple
from folding.protocol import Synapse
from folding.miners.forward import forward
from folding.validators.protein import Protein

bt.trace()

def memory(files: dict):
    total = 0
    for k, v in files.items():
        size_kb = sys.getsizeof(v)/1024
        total += size_kb
        print(f'file {k!r}: {size_kb:.2f} KB')
    print('------')
    print(f'Total: {total:.2f} KB')

### Protein class is contains the protein sequence and the current state of the protein folding simulation.

In [3]:
protein = Protein(max_steps=500)
protein

PDB file 1UBQ.pdb already exists in path '/Users/steffencruz/Desktop/py/opentensor/folding/data/1UBQ'.


Protein(pdb_id=1UBQ, ff=charmm27, box=dodecahedron, output_directory=/Users/steffencruz/Desktop/py/opentensor/folding/data/1UBQ)

### validator is currently responsible for preparing the protein for the simulation.

In [5]:
protein.md_inputs

{'em.gro': 'UBIQUITIN in water\n18916\n    1MET      N    1   4.579   4.396   1.062\n    1MET     H1    2   4.528   4.312   1.024\n    1MET     H2    3   4.654   4.422   0.994\n    1MET     H3    4   4.623   4.370   1.153\n    1MET     CA    5   4.484   4.511   1.075\n    1MET     HA    6   4.451   4.536   0.975\n    1MET     CB    7   4.359   4.471   1.160\n    1MET    HB1    8   4.281   4.548   1.143\n    1MET    HB2    9   4.318   4.375   1.122\n    1MET     CG   10   4.381   4.459   1.313\n    1MET    HG1   11   4.474   4.402   1.332\n    1MET    HG2   12   4.396   4.561   1.356\n    1MET     SD   13   4.244   4.378   1.398\n    1MET     CE   14   4.313   4.379   1.565\n    1MET    HE1   15   4.247   4.322   1.634\n    1MET    HE2   16   4.413   4.331   1.568\n    1MET    HE3   17   4.321   4.482   1.604\n    1MET      C   18   4.545   4.634   1.136\n    1MET      O   19   4.643   4.626   1.210\n    2GLN      N   20   4.487   4.753   1.111\n    2GLN     HN   21   4.406   4.761   1.

In [19]:
memory(protein.md_inputs)


file 'em.gro': 831.43 KB
file 'topol.top': 334.16 KB
file 'posre.itp': 18.54 KB
file 'nvt.mdp': 1.77 KB
file 'npt.mdp': 2.00 KB
file 'md.mdp': 2.40 KB
------
Total: 1190.30 KB


# Simulation using only Synapse

In [9]:
synapse = Synapse(pdb_id=protein.pdb_id, md_inputs=protein.md_inputs)#, mdrun_args='-maxh 0.01')
synapse

Synapse(pdb_id='1UBQ', md_inputs={'em.gro': 'UBIQUITIN in water\n18916\n    1MET      N    1   4.579   4.396   1.062\n    1MET     H1    2   4.528   4.312   1.024\n    1MET     H2    3   4.654   4.422   0.994\n    1MET     H3    4   4.623   4.370   1.153\n    1MET     CA    5   4.484   4.511   1.075\n    1MET     HA    6   4.451   4.536   0.975\n    1MET     CB    7   4.359   4.471   1.160\n    1MET    HB1    8   4.281   4.548   1.143\n    1MET    HB2    9   4.318   4.375   1.122\n    1MET     CG   10   4.381   4.459   1.313\n    1MET    HG1   11   4.474   4.402   1.332\n    1MET    HG2   12   4.396   4.561   1.356\n    1MET     SD   13   4.244   4.378   1.398\n    1MET     CE   14   4.313   4.379   1.565\n    1MET    HE1   15   4.247   4.322   1.634\n    1MET    HE2   16   4.413   4.331   1.568\n    1MET    HE3   17   4.321   4.482   1.604\n    1MET      C   18   4.545   4.634   1.136\n    1MET      O   19   4.643   4.626   1.210\n    2GLN      N   20   4.487   4.753   1.111\n    2GLN

### Simulate the miner receiving the synapse and performing the md simulation.

In [20]:
forward(synapse)

2023-11-10 12:48:47.150 |       INFO       | Running GROMACS simulation for protein: 1UBQ with files dict_keys(['em.gro', 'topol.top', 'posre.itp', 'nvt.mdp', 'npt.mdp', 'md.mdp']) mdrun_args: 


  0%|          | 0/6 [00:00<?, ?it/s]

2023-11-10 12:48:47.166 |       INFO       | Running GROMACS command: gmx grompp -f nvt.mdp -c em.gro -r em.gro -p topol.top -o nvt.tpr


                 :-) GROMACS - gmx grompp, 2023.3-Homebrew (-:

Executable:   /usr/local/bin/../Cellar/gromacs/2023.3/bin/gmx
Data prefix:  /usr/local/bin/../Cellar/gromacs/2023.3
Working dir:  /Users/steffencruz/Desktop/py/opentensor/folding/examples/data/miner/1UBQ/data/miner/1UBQ
Command line:
  gmx grompp -f nvt.mdp -c em.gro -r em.gro -p topol.top -o nvt.tpr

Ignoring obsolete mdp entry 'title'
Generating 1-4 interactions: fudge = 1
Number of degrees of freedom in T-Coupling group System is 38431.00

NOTE 1 [file nvt.mdp]:
  Removing center of mass motion in the presence of position restraints
  might cause artifacts. When you are using position restraints to
  equilibrate a macro-molecule, the artifacts are usually negligible.


There was 1 NOTE

GROMACS reminds you: "Money won't buy happiness, but it will pay the salaries of a large research staff to study the problem." (Bill Vaughan)

 17%|█▋        | 1/6 [00:05<00:25,  5.14s/it]

Setting the LD random seed to -2129921

Generated 20503 of the 20503 non-bonded parameter combinations

Generated 17396 of the 20503 1-4 parameter combinations

Excluding 3 bonded neighbours molecule type 'Protein_chain_A'

turning H bonds into constraints...

Excluding 2 bonded neighbours molecule type 'SOL'

turning H bonds into constraints...

Excluding 2 bonded neighbours molecule type 'SOL'

Setting gen_seed to -1351757969

Velocities were taken from a Maxwell distribution at 300 K
Analysing residue names:
There are:    76    Protein residues
There are:  5895      Water residues
Analysing Protein...

The largest distance between excluded atoms is 0.424 nm between atom 5 and 13

Determining Verlet buffer for a tolerance of 0.005 kJ/mol/ps at 300 K

Calculated rlist for 1x1 atom pair-list as 1.234 nm, buffer size 0.034 nm

Set rlist, assuming 4x4 atom pair-list, to 1.200 nm, buffer size 0.000 nm

Note that mdrun will redetermine rlist based on the actual pair-list setup
Calculating 

...

                 :-) GROMACS - gmx grompp, 2023.3-Homebrew (-:

Executable:   /usr/local/bin/../Cellar/gromacs/2023.3/bin/gmx
Data prefix:  /usr/local/bin/../Cellar/gromacs/2023.3
Working dir:  /Users/steffencruz/Desktop/py/opentensor/folding/examples/data/miner/1UBQ/data/miner/1UBQ
Command line:
  gmx grompp -f md.mdp -c npt.gro -t npt.cpt -p topol.top -o md_0_1.tpr

Ignoring obsolete mdp entry 'title'
Generating 1-4 interactions: fudge = 1
Number of degrees of freedom in T-Coupling group System is 38431.00
Last frame         -1 time    1.000   

GROMACS reminds you: "On the East coast, a purple patch, to show where the jolly pioneers of progress drink the jolly lager-beer" (Joseph Conrad)

 83%|████████▎ | 5/6 [00:22<00:03,  3.79s/it]

Setting the LD random seed to -71368803

Generated 20503 of the 20503 non-bonded parameter combinations

Generated 17396 of the 20503 1-4 parameter combinations

Excluding 3 bonded neighbours molecule type 'Protein_chain_A'

turning H bonds into constraints...

Excluding 2 bonded neighbours molecule type 'SOL'

turning H bonds into constraints...

Excluding 2 bonded neighbours molecule type 'SOL'
Analysing residue names:
There are:    76    Protein residues
There are:  5895      Water residues
Analysing Protein...

The largest distance between excluded atoms is 0.431 nm between atom 5 and 13

Determining Verlet buffer for a tolerance of 0.005 kJ/mol/ps at 300 K

Calculated rlist for 1x1 atom pair-list as 1.234 nm, buffer size 0.034 nm

Set rlist, assuming 4x4 atom pair-list, to 1.200 nm, buffer size 0.000 nm

Note that mdrun will redetermine rlist based on the actual pair-list setup

Reading Coordinates, Velocities and Box size from old trajectory

Will read whole trajectory

Using fra

                  :-) GROMACS - gmx mdrun, 2023.3-Homebrew (-:

Executable:   /usr/local/bin/../Cellar/gromacs/2023.3/bin/gmx
Data prefix:  /usr/local/bin/../Cellar/gromacs/2023.3
Working dir:  /Users/steffencruz/Desktop/py/opentensor/folding/examples/data/miner/1UBQ/data/miner/1UBQ
Command line:
  gmx mdrun -deffnm md_0_1

Reading file md_0_1.tpr, VERSION 2023.3-Homebrew (single precision)
Changing nstlist from 10 to 80, rlist from 1.2 to 1.328

Using 1 MPI thread
Using 12 OpenMP threads 

starting mdrun 'UBIQUITIN in water'
500 steps,      1.0 ps.

Writing final coordinates.

               Core t (s)   Wall t (s)        (%)
       Time:       85.595        7.133     1200.0
                 (ns/day)    (hour/ns)
Performance:       12.137        1.977

GROMACS reminds you: "In science it often happens that scientists say, 'You know that's a really good argument; my position is mistaken,' and then they would actually change their minds and you never hear that old view from them again. 

2023-11-10 12:49:17.796 |       INFO       | Attaching file: md_0_1.log to synapse.md_output
2023-11-10 12:49:17.797 |       INFO       | Attaching file: md_0_1.xtc to synapse.md_output
2023-11-10 12:49:17.798 |       INFO       | Attaching file: md_0_1.gro to synapse.md_output
2023-11-10 12:49:17.799 |       INFO       | Attaching file: md_0_1.tpr to synapse.md_output
2023-11-10 12:49:17.800 |       INFO       | Attaching file: md_0_1.cpt to synapse.md_output
2023-11-10 12:49:17.800 |       INFO       | Attaching file: md_0_1.edr to synapse.md_output


Synapse(pdb_id='1UBQ', md_inputs={'em.gro': 'UBIQUITIN in water\n18916\n    1MET      N    1   4.579   4.396   1.062\n    1MET     H1    2   4.528   4.312   1.024\n    1MET     H2    3   4.654   4.422   0.994\n    1MET     H3    4   4.623   4.370   1.153\n    1MET     CA    5   4.484   4.511   1.075\n    1MET     HA    6   4.451   4.536   0.975\n    1MET     CB    7   4.359   4.471   1.160\n    1MET    HB1    8   4.281   4.548   1.143\n    1MET    HB2    9   4.318   4.375   1.122\n    1MET     CG   10   4.381   4.459   1.313\n    1MET    HG1   11   4.474   4.402   1.332\n    1MET    HG2   12   4.396   4.561   1.356\n    1MET     SD   13   4.244   4.378   1.398\n    1MET     CE   14   4.313   4.379   1.565\n    1MET    HE1   15   4.247   4.322   1.634\n    1MET    HE2   16   4.413   4.331   1.568\n    1MET    HE3   17   4.321   4.482   1.604\n    1MET      C   18   4.545   4.634   1.136\n    1MET      O   19   4.643   4.626   1.210\n    2GLN      N   20   4.487   4.753   1.111\n    2GLN

### Simulation results are attached to synapse

In [21]:
memory(synapse.md_output)

file 'md_0_1.log': 25.49 KB
file 'md_0_1.xtc': 66.07 KB
file 'md_0_1.gro': 1274.76 KB
file 'md_0_1.tpr': 780.58 KB
file 'md_0_1.cpt': 445.34 KB
file 'md_0_1.edr': 1.92 KB
------
Total: 2594.16 KB


### Perform reward calculation for miner

In [18]:
reward = protein.reward(synapse.md_output)

reward

  0%|          | 0/1 [00:00<?, ?it/s]                 :-) GROMACS - gmx energy, 2023.3-Homebrew (-:

Executable:   /usr/local/bin/../Cellar/gromacs/2023.3/bin/gmx
Data prefix:  /usr/local/bin/../Cellar/gromacs/2023.3
Working dir:  /Users/steffencruz/Desktop/py/opentensor/folding/examples/data/miner/1UBQ
Command line:
  gmx energy -f md_0_1.edr -o free_energy.xvg

Opened md_0_1.edr as single precision energy file

Select the terms you want from the following list by
selecting either (part of) the name or the number or a combination.
End your selection with an empty line or a zero.
-------------------------------------------------------------------
  1  Bond             2  U-B              3  Proper-Dih.      4  Improper-Dih. 
  5  CMAP-Dih.        6  LJ-14            7  Coulomb-14       8  LJ-(SR)       
  9  Coulomb-(SR)    10  Coul.-recip.    11  Potential       12  Kinetic-En.   
 13  Total-Energy    14  Conserved-En.   15  Temperature     16  Pressure      
 17  Constr.-rmsd    18  


Statistics over 501 steps [ 0.0000 through 1.0000 ps ], 1 data sets
All statistics are over 6 points

Energy                      Average   Err.Est.       RMSD  Tot-Drift
-------------------------------------------------------------------------------
Total Energy                -243045         --    1016.74    3787.06  (kJ/mol)


242731.171875

# Simulation using Dendrite

In [ ]:

def blacklist( synapse: Synapse ) -> Tuple[bool, str]:
    """
    Determines if the provided synapse should be blacklisted.

    Args:
        synapse (Prompting): The input synapse to be evaluated.

    Returns:
        Tuple[bool, str]: A tuple containing a boolean that indicates whether the synapse is blacklisted,
                          and a string providing the reason.
    """
    return False, ""

def priority( synapse: Synapse ) -> float:
    """
    Determines the priority of the provided synapse.

    Args:
        synapse (Prompting): The input synapse to be evaluated.

    Returns:
        float: The priority value of the synapse, with higher values indicating higher priority.
    """
    return 0.0

In [ ]:
# Create an Axon instance on port 8099.
axon = bt.axon(port=8098)

# Attach the forward, blacklist, and priority functions to the Axon.
# forward_fn: The function to handle forwarding logic.
# blacklist_fn: The function to determine if a request should be blacklisted.
# priority_fn: The function to determine the priority of the request.
axon.attach(
    forward_fn=forward,
    blacklist_fn=blacklist,
    priority_fn=priority
)

# Start the Axon to begin listening for requests.
axon.start()

# Create a Dendrite instance to handle client-side communication.
dendrite = bt.dendrite()

# Send a request to the Axon using the Dendrite, passing in a StreamPrompting instance with roles and messages.
# The response is awaited, as the Dendrite communicates asynchronously with the Axon.
resp = await dendrite(
    [axon],
    Synapse(pdb_id=protein.pdb_id, md_inputs=protein.md_inputs),
    deserialize=True
)

# The response object contains the result of the prompting operation.
resp

# Outlook
We have demonstrated that a molecular dynamics simulation can be carried out in the context of a subnet.

## Remaining Steps
- Use Gromacs python API (https://gromacs-py.readthedocs.io/en/latest/notebook/00_basic_example.html, https://github.com/Becksteinlab/GromacsWrapper)
- Run on staging
- Run on testnet
- Run on mainnet


## Opportunities for Improvements
- Improved customization of input files (e.g. force field, box, mdp templates)
- Performance optimization (file usage, simulation length, parallelization)
- Allow for different miners (e.g. AI models versus GPU models versus CPU models)
- Perturbation of the structure (e.g. mutation) to prevent lookup attacks
- More complex scoring function (e.g. based on RMSD)
- More complex simulation (e.g. folding of a protein with multiple chains)

